契約期間２&フル間取りでXGBoostのクロスバリデーションを行う。

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
import xgboost
from sklearn.model_selection import KFold

###訓練データの読み込み
house_age = pd.read_csv('house_age.csv')
area_size = pd.read_csv('area_size.csv')
room_arrange = pd.read_csv('room_arrange.csv')
contract_span = pd.read_csv('contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('reg_rent.csv')
floor_scores = pd.read_csv('floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('stations.csv')
minits = pd.read_csv('minits.csv')
addresses = pd.read_csv('addresses.csv')
room_arrange = pd.read_csv('room_arrange.csv')
buildings = pd.read_csv('buildings.csv')

rent = pd.read_csv('rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('test_house_age.csv')
test_area_size = pd.read_csv('test_area_size.csv')
test_room_arrange = pd.read_csv('test_room_arrange.csv')
test_contract_span = pd.read_csv('test_contract_span.csv')
test_contract_span2 = pd.read_csv('test_contract_span2.csv')
test_reg_rent = pd.read_csv('test_reg_rent.csv')
test_floor_scores = pd.read_csv('test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('test_capital_floor_scores2.csv')
test_stations = pd.read_csv('test_stations.csv')
test_minits = pd.read_csv('test_minits.csv')
test_addresses = pd.read_csv('test_addresses.csv')
test_room_arrange = pd.read_csv('test_room_arrange.csv')
test_buildings = pd.read_csv('test_buildings.csv')

Duplicate key in file PosixPath('/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/matplotlib/mpl-data/matplotlibrc'), line 258 ('font.family : IPAexGothic')
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


チューニングを行う。

In [4]:
X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, addresses, room_arrange], axis=1)
y_train = rent

X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.3, random_state=0)

X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_addresses, test_room_arrange], axis=1)

def objective(trial):
    
    xgb_reg = xgboost.XGBRegressor(
    #目的関数の指定 初期値も二乗誤差です
                       objective='reg:linear',
                       #学習のラウンド数 early_stoppingを利用するので多めに指定
                       n_estimators=50000,
                       #boosterに何を用いるか 初期値もgbtreeです
                       booster='gbtree',
                       #学習率
                       learning_rate=0.05,
                       #木の最大深さ
                       max_depth=trial.suggest_int('max_depth', 1, 10),
                       #シード値
                       random_state=0,
                        #正則化
                       reg_alfa=trial.suggest_float('reg_alfa', 0.0000001, 0.0001, log=True),

                       sub_sample=trial.suggest_float('sub_sample', 0.01, 0.9, log=True),

                       colsample_bytree=trial.suggest_float('colsample_bytree', 0.01, 0.9, log=True),

                       min_child_weight=trial.suggest_float('min_child_weight', 0.01, 10.0, log=True),
    )

    xgb_reg.fit(X_train, y_train, eval_set=[(X_valid, y_valid)], early_stopping_rounds=10)
    y_pred_valid = xgb_reg.predict(X_valid)

    loss = mean_squared_error(y_valid, y_pred_valid, squared=False)
    return loss

In [5]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)
study.best_params

[I 2022-09-11 19:35:00,696] A new study created in memory with name: no-name-022e336a-daa0-430a-9ea4-25e361a3c12d


[19:35:00] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[19:35:00] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:133361.18197
[1]	validation_0-rmse:128557.85334
[2]	validation_0-rmse:123888.73198
[3]	validation_0-rmse:119165.61808
[4]	validation_0-rmse:114909.17270
[5]	validation_0-rmse:111277.62356
[6]	validation_0-rmse:107570.49423
[7]	validation_0-rmse:104403.28986
[8]	validation_0-rmse:101468.31058
[9]

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[35]	validation_0-rmse:61968.81106
[36]	validation_0-rmse:61446.06189
[37]	validation_0-rmse:61122.21143
[38]	validation_0-rmse:60710.57102
[39]	validation_0-rmse:60452.54393
[40]	validation_0-rmse:60239.90601
[41]	validation_0-rmse:59903.41899
[42]	validation_0-rmse:59711.62022
[43]	validation_0-rmse:59354.72912
[44]	validation_0-rmse:58098.31262
[45]	validation_0-rmse:57969.68529
[46]	validation_0-rmse:57529.52096
[47]	validation_0-rmse:57423.15208
[48]	validation_0-rmse:57293.08848
[49]	validation_0-rmse:57153.65112
[50]	validation_0-rmse:57016.08097
[51]	validation_0-rmse:56763.49232
[52]	validation_0-rmse:56403.06133
[53]	validation_0-rmse:56279.63135
[54]	validation_0-rmse:55799.46794
[55]	validation_0-rmse:55551.11555
[56]	validation_0-rmse:55121.07850
[57]	validation_0-rmse:54764.28448
[58]	validation_0-rmse:54673.37726
[59]	validation_0-rmse:54608.28032
[60]	validation_0-rmse:54574.93778
[61]	validation_0-rmse:54262.24224
[62]	validation_0-rmse:54020.33611
[63]	validation_0-rm

[I 2022-09-11 19:35:06,167] Trial 0 finished with value: 34818.31823078172 and parameters: {'max_depth': 6, 'reg_alfa': 1.3981961408994034e-05, 'sub_sample': 0.1506419097075089, 'colsample_bytree': 0.11610044354231804, 'min_child_weight': 0.18662266976517972}. Best is trial 0 with value: 34818.31823078172.


...

[19:44:20] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[19:44:20] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:133361.18197
[1]	validation_0-rmse:128557.85334
[2]	validation_0-rmse:123888.73198
[3]	validation_0-rmse:119165.61808
[4]	validation_0-rmse:114909.17270
[5]	validation_0-rmse:111277.62356
[6]	validation_0-rmse:107570.49423
[7]	validation_0-rmse:104445.92740
[8]	validation_0-rmse:101512.66327
[9]

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[37]	validation_0-rmse:61307.27700
[38]	validation_0-rmse:60897.54047
[39]	validation_0-rmse:60640.60030
[40]	validation_0-rmse:60442.79297
[41]	validation_0-rmse:60108.08365
[42]	validation_0-rmse:59945.35985
[43]	validation_0-rmse:59596.12104
[44]	validation_0-rmse:58354.29063
[45]	validation_0-rmse:58226.33899
[46]	validation_0-rmse:57784.14340
[47]	validation_0-rmse:57678.33130
[48]	validation_0-rmse:57548.94327
[49]	validation_0-rmse:57410.29114
[50]	validation_0-rmse:57327.95771
[51]	validation_0-rmse:57074.71604
[52]	validation_0-rmse:56711.91497
[53]	validation_0-rmse:56589.12526
[54]	validation_0-rmse:56107.39047
[55]	validation_0-rmse:55912.62522
[56]	validation_0-rmse:55480.87419
[57]	validation_0-rmse:55122.13392
[58]	validation_0-rmse:55072.54849
[59]	validation_0-rmse:55008.12566
[60]	validation_0-rmse:54975.22051
[61]	validation_0-rmse:54660.31927
[62]	validation_0-rmse:54414.40766
[63]	validation_0-rmse:54070.83383
[64]	validation_0-rmse:54010.06384
[65]	validation_0-rm

[I 2022-09-11 19:44:26,001] Trial 39 finished with value: 36078.882392985615 and parameters: {'max_depth': 5, 'reg_alfa': 4.811094460982537e-07, 'sub_sample': 0.031410456573584364, 'colsample_bytree': 0.012983836916378706, 'min_child_weight': 0.20102491014919222}. Best is trial 1 with value: 23093.509985916466.


{'max_depth': 7,
 'reg_alfa': 2.054762512591133e-06,
 'sub_sample': 0.5530198332197337,
 'colsample_bytree': 0.7642417009494488,
 'min_child_weight': 0.14135935551752302}

チューニングしたパラメータを行う。

In [7]:
X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, addresses, room_arrange[["部屋数","L","D","K","S"]]], axis=1)
y_train = rent

# X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.3, random_state=0)

X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_addresses, test_room_arrange[["部屋数","L","D","K","S"]]], axis=1)

cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    xgb_reg = xgboost.XGBRegressor(
        #目的関数の指定 初期値も二乗誤差です
                        objective='reg:linear',
                        #学習のラウンド数 early_stoppingを利用するので多めに指定
                        n_estimators=50000,
                        #boosterに何を用いるか 初期値もgbtreeです
                        booster='gbtree',
                        #学習率
                        learning_rate=0.05,
                        #木の最大深さ
                        max_depth=7,
                        #シード値
                        random_state=0,
                            #正則化
                        reg_alfa=2.054762512591133e-06,

                        sub_sample=0.5530198332197337,

                        colsample_bytree=0.7642417009494488,

                        min_child_weight=0.14135935551752302
    )
    xgb_reg.fit(X_tr, y_tr, eval_set=[(X_val, y_val)], early_stopping_rounds=10)
y_pred = xgb_reg.predict(X_test)


[19:49:48] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[19:49:48] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:132565.58842
[1]	validation_0-rmse:126650.14447
[2]	validation_0-rmse:121107.24070
[3]	validation_0-rmse:115799.37748
[4]	validation_0-rmse:110981.84982
[5]	validation_0-rmse:106400.85105
[6]	validation_0-rmse:101849.13745
[7]	validation_0-rmse:97539.63943
[8]	validation_0-rmse:93418.79629
[9]	v

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[15]	validation_0-rmse:71180.92067
[16]	validation_0-rmse:68569.92215
[17]	validation_0-rmse:66096.38690
[18]	validation_0-rmse:63790.77657
[19]	validation_0-rmse:61599.28034
[20]	validation_0-rmse:59680.57700
[21]	validation_0-rmse:57763.18435
[22]	validation_0-rmse:56211.07039
[23]	validation_0-rmse:54569.78817
[24]	validation_0-rmse:53131.65252
[25]	validation_0-rmse:51676.11348
[26]	validation_0-rmse:50233.53663
[27]	validation_0-rmse:49022.52469
[28]	validation_0-rmse:47810.04225
[29]	validation_0-rmse:46786.28632
[30]	validation_0-rmse:45661.30819
[31]	validation_0-rmse:44735.75939
[32]	validation_0-rmse:43896.50740
[33]	validation_0-rmse:42960.82986
[34]	validation_0-rmse:42165.62298
[35]	validation_0-rmse:41449.70513
[36]	validation_0-rmse:40841.96505
[37]	validation_0-rmse:40135.18677
[38]	validation_0-rmse:39546.06681
[39]	validation_0-rmse:39013.40152
[40]	validation_0-rmse:38508.41165
[41]	validation_0-rmse:38066.95715
[42]	validation_0-rmse:37615.52224
[43]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[16]	validation_0-rmse:68111.82137
[17]	validation_0-rmse:65657.95518
[18]	validation_0-rmse:63349.58589
[19]	validation_0-rmse:61167.24591
[20]	validation_0-rmse:59333.41679
[21]	validation_0-rmse:57404.70248
[22]	validation_0-rmse:55793.09132
[23]	validation_0-rmse:54072.88074
[24]	validation_0-rmse:52636.07133
[25]	validation_0-rmse:51113.69582
[26]	validation_0-rmse:49617.28166
[27]	validation_0-rmse:48435.51412
[28]	validation_0-rmse:47135.73125
[29]	validation_0-rmse:46134.55118
[30]	validation_0-rmse:45004.36903
[31]	validation_0-rmse:44121.65184
[32]	validation_0-rmse:43340.71990
[33]	validation_0-rmse:42428.56869
[34]	validation_0-rmse:41543.44996
[35]	validation_0-rmse:40895.02591
[36]	validation_0-rmse:40256.23446
[37]	validation_0-rmse:39533.89730
[38]	validation_0-rmse:39014.40773
[39]	validation_0-rmse:38545.16273
[40]	validation_0-rmse:38101.21711
[41]	validation_0-rmse:37684.04649
[42]	validation_0-rmse:37189.93659
[43]	validation_0-rmse:36840.22573
[44]	validation_0-rm

...

[17]	validation_0-rmse:64458.43568
[18]	validation_0-rmse:61926.03220
[19]	validation_0-rmse:59595.47237
[20]	validation_0-rmse:57630.68104
[21]	validation_0-rmse:55556.36761
[22]	validation_0-rmse:53797.17909
[23]	validation_0-rmse:51928.14489
[24]	validation_0-rmse:50419.92938
[25]	validation_0-rmse:48759.13020
[26]	validation_0-rmse:47173.75826
[27]	validation_0-rmse:45882.87267
[28]	validation_0-rmse:44597.74823
[29]	validation_0-rmse:43522.82148
[30]	validation_0-rmse:42294.15955
[31]	validation_0-rmse:41368.30026
[32]	validation_0-rmse:40466.02136
[33]	validation_0-rmse:39495.46170
[34]	validation_0-rmse:38661.58034
[35]	validation_0-rmse:37947.70000
[36]	validation_0-rmse:37267.49482
[37]	validation_0-rmse:36550.42486
[38]	validation_0-rmse:36008.16192
[39]	validation_0-rmse:35490.80922
[40]	validation_0-rmse:35014.57780
[41]	validation_0-rmse:34541.34719
[42]	validation_0-rmse:34113.17815
[43]	validation_0-rmse:33752.11500
[44]	validation_0-rmse:33294.43396
[45]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[15]	validation_0-rmse:68974.06733
[16]	validation_0-rmse:66277.01553
[17]	validation_0-rmse:63768.46083
[18]	validation_0-rmse:61357.04651
[19]	validation_0-rmse:59095.75707
[20]	validation_0-rmse:57185.91684
[21]	validation_0-rmse:55194.11735
[22]	validation_0-rmse:53531.05739
[23]	validation_0-rmse:51782.48778
[24]	validation_0-rmse:50285.43621
[25]	validation_0-rmse:48705.55662
[26]	validation_0-rmse:47216.30122
[27]	validation_0-rmse:46010.36851
[28]	validation_0-rmse:44678.36991
[29]	validation_0-rmse:43647.34513
[30]	validation_0-rmse:42484.81099
[31]	validation_0-rmse:41590.56849
[32]	validation_0-rmse:40784.46031
[33]	validation_0-rmse:39818.75600
[34]	validation_0-rmse:38925.55690
[35]	validation_0-rmse:38237.04039
[36]	validation_0-rmse:37605.05610
[37]	validation_0-rmse:36866.49264
[38]	validation_0-rmse:36318.82674
[39]	validation_0-rmse:35803.64634
[40]	validation_0-rmse:35331.06345
[41]	validation_0-rmse:34939.86599
[42]	validation_0-rmse:34538.33394
[43]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[16]	validation_0-rmse:68741.14152
[17]	validation_0-rmse:66153.81645
[18]	validation_0-rmse:63635.41022
[19]	validation_0-rmse:61331.09193
[20]	validation_0-rmse:59355.72554
[21]	validation_0-rmse:57238.31478
[22]	validation_0-rmse:55561.14528
[23]	validation_0-rmse:53805.91868
[24]	validation_0-rmse:52349.38028
[25]	validation_0-rmse:50665.86029
[26]	validation_0-rmse:49080.53372
[27]	validation_0-rmse:47851.18199
[28]	validation_0-rmse:46563.47607
[29]	validation_0-rmse:45545.24913
[30]	validation_0-rmse:44292.70683
[31]	validation_0-rmse:43386.75080
[32]	validation_0-rmse:42567.92966
[33]	validation_0-rmse:41487.28463
[34]	validation_0-rmse:40520.53585
[35]	validation_0-rmse:39861.68287
[36]	validation_0-rmse:39253.46128
[37]	validation_0-rmse:38454.30200
[38]	validation_0-rmse:37938.12653
[39]	validation_0-rmse:37326.81671
[40]	validation_0-rmse:36875.96716
[41]	validation_0-rmse:36445.45771
[42]	validation_0-rmse:36056.61122
[43]	validation_0-rmse:35675.55344
[44]	validation_0-rm

In [8]:
df = pd.read_csv('test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('XGB_cv_result.csv',index=False)

### 「地価」をXGBoostに入力する

In [1]:
import pandas as pd


df_adachi = pd.read_csv('../data/handmade_data/block_aveprice_adachi2019.csv')
df_arakawa = pd.read_csv('../data/handmade_data/block_aveprice_arakawa2019.csv')
df_bunkyo = pd.read_csv('../data/handmade_data/block_aveprice_bunkyo2019.csv')
df_chiyoda = pd.read_csv('../data/handmade_data/block_aveprice_chiyoda2019.csv')
df_chuo = pd.read_csv('../data/handmade_data/block_aveprice_chuo2019.csv')
df_edogawa = pd.read_csv('../data/handmade_data/block_aveprice_edogawa2019.csv')
df_itabashi = pd.read_csv('../data/handmade_data/block_aveprice_itabashi2019.csv')
df_katsushika = pd.read_csv('../data/handmade_data/block_aveprice_katsushika2019.csv')
df_kita = pd.read_csv('../data/handmade_data/block_aveprice_kita2019.csv')
df_koto = pd.read_csv('../data/handmade_data/block_aveprice_koto2019.csv')
df_meguro = pd.read_csv('../data/handmade_data/block_aveprice_meguro2019.csv')
df_minato = pd.read_csv('../data/handmade_data/block_aveprice_minato2019.csv')
df_nakano = pd.read_csv('../data/handmade_data/block_aveprice_nakano2019.csv')
df_nerima = pd.read_csv('../data/handmade_data/block_aveprice_nerima2019.csv')
df_ota = pd.read_csv('../data/handmade_data/block_aveprice_ota2019.csv')
df_setagaya = pd.read_csv('../data/handmade_data/block_aveprice_setagaya2019.csv')
df_shibuya = pd.read_csv('../data/handmade_data/block_aveprice_shibuya2019.csv')
df_shinagawa = pd.read_csv('../data/handmade_data/block_aveprice_shinagawa2019.csv')
df_shinjuku = pd.read_csv('../data/handmade_data/block_aveprice_shinjuku2019.csv')
df_suginami = pd.read_csv('../data/handmade_data/block_aveprice_suginami2019.csv')
df_sumida = pd.read_csv('../data/handmade_data/block_aveprice_sumida2019.csv')
df_taito = pd.read_csv('../data/handmade_data/block_aveprice_taito2019.csv')
df_toshima = pd.read_csv('../data/handmade_data/block_aveprice_toshima2019.csv')

df_23wards = pd.concat([
    df_adachi,
    df_arakawa,
    df_bunkyo,
    df_chiyoda,
    df_chuo,
    df_edogawa,
    df_itabashi,
    df_katsushika,
    df_kita,
    df_koto,
    df_meguro,
    df_minato,
    df_nakano,
    df_nerima,
    df_ota,
    df_setagaya,
    df_shibuya,
    df_shinjuku,
    df_shinagawa,
    df_suginami,
    df_sumida,
    df_taito,
    df_toshima
],ignore_index=True)

addresses = pd.read_csv('../data/handmade_data/merge_address.csv')
addresses = addresses['所在地']
addresses = pd.DataFrame(addresses)

address_aveprice = pd.merge(addresses, df_23wards, left_on='所在地', right_on='0', how='left')
address_aveprice = address_aveprice[['所在地', '1']]
address_aveprice.columns = [['区町名', '平均地価']]

land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
land_aveprice.columns = ['平均地価']
test_land_aveprice.columns = ['平均地価']


import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]]], axis=1)
y_train = rent
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D","S"]]], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S']

Duplicate key in file PosixPath('/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/matplotlib/mpl-data/matplotlibrc'), line 258 ('font.family : IPAexGothic')
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


チューニングを行う

In [7]:
X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.3, random_state=0)

def objective(trial):
    
    xgb_reg = xgboost.XGBRegressor(
    #目的関数の指定 初期値も二乗誤差です
                       objective='reg:linear',
                       #学習のラウンド数 early_stoppingを利用するので多めに指定
                       n_estimators=50000,
                       #boosterに何を用いるか 初期値もgbtreeです
                       booster='gbtree',
                       #学習率
                       learning_rate=0.05,
                       #木の最大深さ
                       max_depth=trial.suggest_int('max_depth', 1, 10),
                       #シード値
                       random_state=0,
                        #正則化
                       reg_alfa=trial.suggest_float('reg_alfa', 0.0000001, 0.0001, log=True),

                       sub_sample=trial.suggest_float('sub_sample', 0.01, 0.9, log=True),

                       colsample_bytree=trial.suggest_float('colsample_bytree', 0.01, 0.9, log=True),

                       min_child_weight=trial.suggest_float('min_child_weight', 0.01, 10.0, log=True),
    )

    xgb_reg.fit(X_train, y_train, eval_set=[(X_valid, y_valid)], early_stopping_rounds=10)
    y_pred_valid = xgb_reg.predict(X_valid)

    loss = mean_squared_error(y_valid, y_pred_valid, squared=False)
    return loss

In [8]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)

[I 2022-09-14 11:47:23,901] A new study created in memory with name: no-name-a0f079ec-9f0e-4320-87e7-372936b52804


[11:47:23] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[11:47:23] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:133361.18197
[1]	validation_0-rmse:128557.85334
[2]	validation_0-rmse:124144.59361
[3]	validation_0-rmse:119754.65561
[4]	validation_0-rmse:115285.34632
[5]	validation_0-rmse:111666.48644
[6]	validation_0-rmse:107966.69079
[7]	validation_0-rmse:104433.72201
[8]	validation_0-rmse:101502.56725
[9]

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[30]	validation_0-rmse:64813.10588
[31]	validation_0-rmse:64160.82233
[32]	validation_0-rmse:63285.81231
[33]	validation_0-rmse:61687.69217
[34]	validation_0-rmse:61254.97626
[35]	validation_0-rmse:60725.21197
[36]	validation_0-rmse:60058.43252
[37]	validation_0-rmse:59733.49262
[38]	validation_0-rmse:59481.04828
[39]	validation_0-rmse:59219.07496
[40]	validation_0-rmse:58504.73314
[41]	validation_0-rmse:58302.16757
[42]	validation_0-rmse:57661.26939
[43]	validation_0-rmse:57303.64648
[44]	validation_0-rmse:56058.47879
[45]	validation_0-rmse:55765.38785
[46]	validation_0-rmse:55357.42295
[47]	validation_0-rmse:55103.68736
[48]	validation_0-rmse:54970.59463
[49]	validation_0-rmse:54831.78270
[50]	validation_0-rmse:54297.86017
[51]	validation_0-rmse:53940.42555
[52]	validation_0-rmse:53622.23227
[53]	validation_0-rmse:53499.66934
[54]	validation_0-rmse:53084.67009
[55]	validation_0-rmse:52887.29404
[56]	validation_0-rmse:52516.93627
[57]	validation_0-rmse:52358.91188
[58]	validation_0-rm

[I 2022-09-14 11:47:26,399] Trial 0 finished with value: 35547.12602430951 and parameters: {'max_depth': 6, 'reg_alfa': 1.3981961408994034e-05, 'sub_sample': 0.1506419097075089, 'colsample_bytree': 0.11610044354231804, 'min_child_weight': 0.18662266976517972}. Best is trial 0 with value: 35547.12602430951.


...

[I 2022-09-14 11:53:45,724] Trial 38 finished with value: 21978.72916048022 and parameters: {'max_depth': 4, 'reg_alfa': 4.2611934121447075e-07, 'sub_sample': 0.02311353048659629, 'colsample_bytree': 0.7007008902120041, 'min_child_weight': 1.654445194287417}. Best is trial 7 with value: 20372.042354710535.


[11:53:45] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[11:53:45] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:133361.18197
[1]	validation_0-rmse:128557.85334
[2]	validation_0-rmse:124179.12815
[3]	validation_0-rmse:119793.41376
[4]	validation_0-rmse:115325.04702
[5]	validation_0-rmse:111708.05078
[6]	validation_0-rmse:108009.68092
[7]	validation_0-rmse:104526.35468
[8]	validation_0-rmse:101599.00977
[9]

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[41]	validation_0-rmse:58647.55407
[42]	validation_0-rmse:58018.55398
[43]	validation_0-rmse:57666.50497
[44]	validation_0-rmse:56452.69745
[45]	validation_0-rmse:56159.33531
[46]	validation_0-rmse:55749.81227
[47]	validation_0-rmse:55495.74639
[48]	validation_0-rmse:55363.04669
[49]	validation_0-rmse:55224.81177
[50]	validation_0-rmse:54692.85184
[51]	validation_0-rmse:54333.35547
[52]	validation_0-rmse:54011.47762
[53]	validation_0-rmse:53889.14947
[54]	validation_0-rmse:53473.73583
[55]	validation_0-rmse:53310.67063
[56]	validation_0-rmse:52940.66381
[57]	validation_0-rmse:52784.57828
[58]	validation_0-rmse:52335.62168
[59]	validation_0-rmse:52269.71464
[60]	validation_0-rmse:52128.06964
[61]	validation_0-rmse:51998.51652
[62]	validation_0-rmse:51784.75694
[63]	validation_0-rmse:51493.95862
[64]	validation_0-rmse:51437.14674
[65]	validation_0-rmse:51326.37550
[66]	validation_0-rmse:50943.16661
[67]	validation_0-rmse:50843.96239
[68]	validation_0-rmse:50745.75354
[69]	validation_0-rm

[I 2022-09-14 11:53:52,968] Trial 39 finished with value: 33915.06549914918 and parameters: {'max_depth': 5, 'reg_alfa': 4.811094460982537e-07, 'sub_sample': 0.031410456573584364, 'colsample_bytree': 0.012983836916378706, 'min_child_weight': 0.20102491014919222}. Best is trial 7 with value: 20372.042354710535.


In [9]:
study.best_params

{'max_depth': 7,
 'reg_alfa': 6.8594164113286965e-06,
 'sub_sample': 0.16056047423047484,
 'colsample_bytree': 0.6987351856651322,
 'min_child_weight': 1.1103525577197584}

チューニング結果を反映させる

In [12]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    xgb_reg = xgboost.XGBRegressor(
        #目的関数の指定 初期値も二乗誤差です
                        objective='reg:linear',
                        #学習のラウンド数 early_stoppingを利用するので多めに指定
                        n_estimators=50000,
                        #boosterに何を用いるか 初期値もgbtreeです
                        booster='gbtree',
                        #学習率
                        learning_rate=0.05,
                        #木の最大深さ
                        max_depth=7,
                        #シード値
                        random_state=0,
                            #正則化
                        reg_alfa=6.8594164113286965e-06,

                        sub_sample=0.16056047423047484,

                        colsample_bytree=0.6987351856651322,

                        min_child_weight=1.1103525577197584
    )
    xgb_reg.fit(X_tr, y_tr, eval_set=[(X_val, y_val)], early_stopping_rounds=10)
y_pred = xgb_reg.predict(X_test)


[11:55:13] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[11:55:13] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:132382.36015
[1]	validation_0-rmse:126424.57796
[2]	validation_0-rmse:120819.70751
[3]	validation_0-rmse:115291.67431
[4]	validation_0-rmse:110387.34675
[5]	validation_0-rmse:105896.01416
[6]	validation_0-rmse:101187.47991
[7]	validation_0-rmse:96731.19083
[8]	validation_0-rmse:92629.41767
[9]	v

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[17]	validation_0-rmse:64836.89033
[18]	validation_0-rmse:62349.00431
[19]	validation_0-rmse:60009.83634
[20]	validation_0-rmse:57972.48312
[21]	validation_0-rmse:56018.06054
[22]	validation_0-rmse:54373.64228
[23]	validation_0-rmse:52664.58493
[24]	validation_0-rmse:51044.33453
[25]	validation_0-rmse:49400.74502
[26]	validation_0-rmse:47805.36922
[27]	validation_0-rmse:46489.43908
[28]	validation_0-rmse:45147.85151
[29]	validation_0-rmse:44110.37949
[30]	validation_0-rmse:42903.80622
[31]	validation_0-rmse:41826.03698
[32]	validation_0-rmse:40924.41360
[33]	validation_0-rmse:39931.74576
[34]	validation_0-rmse:39037.16409
[35]	validation_0-rmse:38196.63202
[36]	validation_0-rmse:37476.66246
[37]	validation_0-rmse:36700.52234
[38]	validation_0-rmse:36058.41060
[39]	validation_0-rmse:35395.67990
[40]	validation_0-rmse:34830.38610
[41]	validation_0-rmse:34272.34837
[42]	validation_0-rmse:33780.54345
[43]	validation_0-rmse:33359.99471
[44]	validation_0-rmse:32828.51360
[45]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[17]	validation_0-rmse:63893.46852
[18]	validation_0-rmse:61290.39014
[19]	validation_0-rmse:58879.28292
[20]	validation_0-rmse:56887.60477
[21]	validation_0-rmse:54829.66195
[22]	validation_0-rmse:53112.98982
[23]	validation_0-rmse:51357.59365
[24]	validation_0-rmse:49716.74118
[25]	validation_0-rmse:47937.12843
[26]	validation_0-rmse:46318.29147
[27]	validation_0-rmse:44931.65377
[28]	validation_0-rmse:43492.80779
[29]	validation_0-rmse:42424.34057
[30]	validation_0-rmse:41198.10150
[31]	validation_0-rmse:40157.32791
[32]	validation_0-rmse:39314.83467
[33]	validation_0-rmse:38276.51344
[34]	validation_0-rmse:37369.60115
[35]	validation_0-rmse:36482.86151
[36]	validation_0-rmse:35716.97228
[37]	validation_0-rmse:34880.91055
[38]	validation_0-rmse:34217.30837
[39]	validation_0-rmse:33626.29539
[40]	validation_0-rmse:33022.62135
[41]	validation_0-rmse:32468.70358
[42]	validation_0-rmse:31990.89841
[43]	validation_0-rmse:31570.67147
[44]	validation_0-rmse:30945.04338
[45]	validation_0-rm

...

[16]	validation_0-rmse:66093.12887
[17]	validation_0-rmse:63281.36934
[18]	validation_0-rmse:60564.00209
[19]	validation_0-rmse:58030.19641
[20]	validation_0-rmse:55914.84195
[21]	validation_0-rmse:53783.42890
[22]	validation_0-rmse:51975.81554
[23]	validation_0-rmse:50063.62331
[24]	validation_0-rmse:48356.55026
[25]	validation_0-rmse:46614.58306
[26]	validation_0-rmse:44893.64651
[27]	validation_0-rmse:43410.57563
[28]	validation_0-rmse:41949.39190
[29]	validation_0-rmse:40774.12267
[30]	validation_0-rmse:39363.91069
[31]	validation_0-rmse:38251.93310
[32]	validation_0-rmse:37308.91946
[33]	validation_0-rmse:36249.04151
[34]	validation_0-rmse:35328.34475
[35]	validation_0-rmse:34470.04569
[36]	validation_0-rmse:33666.24187
[37]	validation_0-rmse:32756.35295
[38]	validation_0-rmse:32035.64061
[39]	validation_0-rmse:31385.97721
[40]	validation_0-rmse:30789.10972
[41]	validation_0-rmse:30213.28855
[42]	validation_0-rmse:29681.92882
[43]	validation_0-rmse:29194.76460
[44]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[14]	validation_0-rmse:70720.28784
[15]	validation_0-rmse:68085.86415
[16]	validation_0-rmse:65240.26015
[17]	validation_0-rmse:62566.73014
[18]	validation_0-rmse:59999.33581
[19]	validation_0-rmse:57582.95733
[20]	validation_0-rmse:55465.24829
[21]	validation_0-rmse:53467.79331
[22]	validation_0-rmse:51713.60860
[23]	validation_0-rmse:49950.14453
[24]	validation_0-rmse:48342.98484
[25]	validation_0-rmse:46653.85680
[26]	validation_0-rmse:45040.91963
[27]	validation_0-rmse:43703.45505
[28]	validation_0-rmse:42263.67439
[29]	validation_0-rmse:41134.43492
[30]	validation_0-rmse:39860.77847
[31]	validation_0-rmse:38833.45121
[32]	validation_0-rmse:37944.68911
[33]	validation_0-rmse:36904.76539
[34]	validation_0-rmse:36002.00718
[35]	validation_0-rmse:35224.16855
[36]	validation_0-rmse:34495.32145
[37]	validation_0-rmse:33674.01569
[38]	validation_0-rmse:33052.12319
[39]	validation_0-rmse:32462.67505
[40]	validation_0-rmse:31908.41705
[41]	validation_0-rmse:31434.99398
[42]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[15]	validation_0-rmse:70602.17166
[16]	validation_0-rmse:67558.68297
[17]	validation_0-rmse:64752.32990
[18]	validation_0-rmse:62023.05289
[19]	validation_0-rmse:59432.43051
[20]	validation_0-rmse:57284.23498
[21]	validation_0-rmse:55077.83736
[22]	validation_0-rmse:53373.23697
[23]	validation_0-rmse:51521.98102
[24]	validation_0-rmse:49859.01110
[25]	validation_0-rmse:47992.74869
[26]	validation_0-rmse:46201.33295
[27]	validation_0-rmse:44816.57438
[28]	validation_0-rmse:43254.33365
[29]	validation_0-rmse:42129.29938
[30]	validation_0-rmse:40829.07136
[31]	validation_0-rmse:39724.13623
[32]	validation_0-rmse:38748.26782
[33]	validation_0-rmse:37633.29064
[34]	validation_0-rmse:36593.39832
[35]	validation_0-rmse:35655.63286
[36]	validation_0-rmse:34810.89271
[37]	validation_0-rmse:33855.13862
[38]	validation_0-rmse:33178.43705
[39]	validation_0-rmse:32470.98379
[40]	validation_0-rmse:31859.44616
[41]	validation_0-rmse:31308.01592
[42]	validation_0-rmse:30711.96588
[43]	validation_0-rm

In [13]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/XGB_cv_result.csv',index=False)

「賃料」が50万円以上のデータを除いてみる

In [2]:
X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]]], axis=1)
y_train = rent
all_train_DATA = pd.concat([y_train, X_train], axis=1)
all_train_DATA = all_train_DATA[all_train_DATA['賃料'] < 500000]

In [3]:
X_train = all_train_DATA.drop('賃料', axis=1)
y_train = all_train_DATA['賃料']

X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D","S"]]], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S']

In [4]:
X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.2, random_state=0)
cv = KFold(n_splits=5, shuffle=True, random_state=0)

#これより交差検証のためにインデックスを振り直すので、最後にインデックスを元に戻すことに備えて元々のインデックスを退避させておく。
origin_index = X_train.index #origin_index = y_train.indexでも同じこと
X_train = X_train.reset_index()#交差検証のためにインデックス振り直し
X_train = X_train.drop('index', axis=1)##reset_index()をした結果、元のインデックスが"index"列として含まれてしまうので落としておく
y_train = y_train.reset_index()#交差検証のためにインデックス振り直し
y_train = y_train.drop('index',axis=1)##reset_index()をした結果、元のインデックスが"index"列として含まれてしまうので落としておく

cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    xgb_reg = xgboost.XGBRegressor(
        #目的関数の指定 初期値も二乗誤差です
                        objective='reg:linear',
                        #学習のラウンド数 early_stoppingを利用するので多めに指定
                        n_estimators=50000,
                        #boosterに何を用いるか 初期値もgbtreeです
                        booster='gbtree',
                        #学習率
                        learning_rate=0.05,
                        #木の最大深さ
                        max_depth=7,
                        #シード値
                        random_state=0,
                            #正則化
                        reg_alfa=6.8594164113286965e-06,

                        sub_sample=0.16056047423047484,

                        colsample_bytree=0.6987351856651322,

                        min_child_weight=1.1103525577197584
    )
    xgb_reg.fit(X_tr, y_tr, eval_set=[(X_val, y_val)], early_stopping_rounds=10)
y_pred = xgb_reg.predict(X_test)

[23:43:38] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[23:43:38] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:123895.36379
[1]	validation_0-rmse:118082.01331
[2]	validation_0-rmse:112583.52511
[3]	validation_0-rmse:107203.59696
[4]	validation_0-rmse:102303.35315
[5]	validation_0-rmse:97688.17897
[6]	validation_0-rmse:93119.22505
[7]	validation_0-rmse:88768.76702
[8]	validation_0-rmse:84695.81833
[9]	val

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[19]	validation_0-rmse:52038.06585
[20]	validation_0-rmse:49971.94107
[21]	validation_0-rmse:48026.02624
[22]	validation_0-rmse:46238.15710
[23]	validation_0-rmse:44482.63844
[24]	validation_0-rmse:42840.59468
[25]	validation_0-rmse:41192.78000
[26]	validation_0-rmse:39616.69643
[27]	validation_0-rmse:38202.72056
[28]	validation_0-rmse:36830.96498
[29]	validation_0-rmse:35636.63786
[30]	validation_0-rmse:34427.25126
[31]	validation_0-rmse:33321.49542
[32]	validation_0-rmse:32350.03331
[33]	validation_0-rmse:31336.26778
[34]	validation_0-rmse:30454.66590
[35]	validation_0-rmse:29594.51896
[36]	validation_0-rmse:28787.28675
[37]	validation_0-rmse:27955.26123
[38]	validation_0-rmse:27276.54276
[39]	validation_0-rmse:26623.48280
[40]	validation_0-rmse:26041.61131
[41]	validation_0-rmse:25458.45061
[42]	validation_0-rmse:24923.16650
[43]	validation_0-rmse:24437.10077
[44]	validation_0-rmse:23920.56802
[45]	validation_0-rmse:23446.56394
[46]	validation_0-rmse:22978.94528
[47]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[15]	validation_0-rmse:61650.71989
[16]	validation_0-rmse:58908.90545
[17]	validation_0-rmse:56313.62428
[18]	validation_0-rmse:53848.82704
[19]	validation_0-rmse:51506.98447
[20]	validation_0-rmse:49422.65802
[21]	validation_0-rmse:47425.76813
[22]	validation_0-rmse:45638.86428
[23]	validation_0-rmse:43884.67756
[24]	validation_0-rmse:42252.92681
[25]	validation_0-rmse:40580.03121
[26]	validation_0-rmse:38985.89052
[27]	validation_0-rmse:37589.84178
[28]	validation_0-rmse:36192.75123
[29]	validation_0-rmse:34993.88349
[30]	validation_0-rmse:33789.48501
[31]	validation_0-rmse:32695.04900
[32]	validation_0-rmse:31728.72201
[33]	validation_0-rmse:30725.59912
[34]	validation_0-rmse:29831.65086
[35]	validation_0-rmse:28976.76015
[36]	validation_0-rmse:28174.32092
[37]	validation_0-rmse:27361.63083
[38]	validation_0-rmse:26666.82195
[39]	validation_0-rmse:26016.46449
[40]	validation_0-rmse:25421.68774
[41]	validation_0-rmse:24840.55117
[42]	validation_0-rmse:24315.19848
[43]	validation_0-rm

...

[13]	validation_0-rmse:67523.86303
[14]	validation_0-rmse:64605.26256
[15]	validation_0-rmse:61954.51000
[16]	validation_0-rmse:59181.55313
[17]	validation_0-rmse:56591.47987
[18]	validation_0-rmse:54104.89308
[19]	validation_0-rmse:51728.62248
[20]	validation_0-rmse:49669.58175
[21]	validation_0-rmse:47718.77939
[22]	validation_0-rmse:45937.52181
[23]	validation_0-rmse:44142.07410
[24]	validation_0-rmse:42457.19204
[25]	validation_0-rmse:40746.38991
[26]	validation_0-rmse:39115.38319
[27]	validation_0-rmse:37694.86014
[28]	validation_0-rmse:36292.36873
[29]	validation_0-rmse:35082.13433
[30]	validation_0-rmse:33818.72646
[31]	validation_0-rmse:32702.39071
[32]	validation_0-rmse:31747.59041
[33]	validation_0-rmse:30709.18327
[34]	validation_0-rmse:29805.17376
[35]	validation_0-rmse:28928.11642
[36]	validation_0-rmse:28091.69762
[37]	validation_0-rmse:27250.73245
[38]	validation_0-rmse:26541.49444
[39]	validation_0-rmse:25863.07336
[40]	validation_0-rmse:25257.98129
[41]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[14]	validation_0-rmse:64130.12857
[15]	validation_0-rmse:61472.79216
[16]	validation_0-rmse:58721.96614
[17]	validation_0-rmse:56125.75358
[18]	validation_0-rmse:53665.95590
[19]	validation_0-rmse:51340.04639
[20]	validation_0-rmse:49244.71418
[21]	validation_0-rmse:47243.62115
[22]	validation_0-rmse:45422.36443
[23]	validation_0-rmse:43635.01879
[24]	validation_0-rmse:41951.94329
[25]	validation_0-rmse:40263.88793
[26]	validation_0-rmse:38658.03952
[27]	validation_0-rmse:37209.91934
[28]	validation_0-rmse:35810.33627
[29]	validation_0-rmse:34606.41321
[30]	validation_0-rmse:33371.92289
[31]	validation_0-rmse:32225.78260
[32]	validation_0-rmse:31248.65739
[33]	validation_0-rmse:30221.46354
[34]	validation_0-rmse:29299.54986
[35]	validation_0-rmse:28407.03905
[36]	validation_0-rmse:27570.49387
[37]	validation_0-rmse:26746.41869
[38]	validation_0-rmse:26030.78481
[39]	validation_0-rmse:25361.08643
[40]	validation_0-rmse:24757.29116
[41]	validation_0-rmse:24169.83173
[42]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[13]	validation_0-rmse:67437.59221
[14]	validation_0-rmse:64493.85389
[15]	validation_0-rmse:61847.76786
[16]	validation_0-rmse:59103.75653
[17]	validation_0-rmse:56546.15044
[18]	validation_0-rmse:54089.76166
[19]	validation_0-rmse:51750.96420
[20]	validation_0-rmse:49663.66068
[21]	validation_0-rmse:47732.15681
[22]	validation_0-rmse:45957.74207
[23]	validation_0-rmse:44197.87231
[24]	validation_0-rmse:42516.44433
[25]	validation_0-rmse:40867.73112
[26]	validation_0-rmse:39288.29356
[27]	validation_0-rmse:37877.56266
[28]	validation_0-rmse:36496.25138
[29]	validation_0-rmse:35295.35255
[30]	validation_0-rmse:34096.86409
[31]	validation_0-rmse:33000.70438
[32]	validation_0-rmse:32046.73748
[33]	validation_0-rmse:31052.31521
[34]	validation_0-rmse:30160.05409
[35]	validation_0-rmse:29311.60534
[36]	validation_0-rmse:28494.86775
[37]	validation_0-rmse:27694.31805
[38]	validation_0-rmse:26989.36819
[39]	validation_0-rmse:26350.03137
[40]	validation_0-rmse:25765.54107
[41]	validation_0-rm

In [5]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/XGB_cv_result.csv',index=False)

### 大きい「面積」にフラグを立ててみる

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]], over100m2, bt75and100m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D","S"]], test_over100m2, test_bt75and100m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S', '100m^2以上', '75m^2以上100m^2未満']

Duplicate key in file PosixPath('/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/matplotlib/mpl-data/matplotlibrc'), line 258 ('font.family : IPAexGothic')
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.2, random_state=0)
# cv = KFold(n_splits=5, shuffle=True, random_state=0)

# #これより交差検証のためにインデックスを振り直すので、最後にインデックスを元に戻すことに備えて元々のインデックスを退避させておく。
# origin_index = X_train.index #origin_index = y_train.indexでも同じこと
# X_train = X_train.reset_index()#交差検証のためにインデックス振り直し
# X_train = X_train.drop('index', axis=1)##reset_index()をした結果、元のインデックスが"index"列として含まれてしまうので落としておく
# y_train = y_train.reset_index()#交差検証のためにインデックス振り直し
# y_train = y_train.drop('index',axis=1)##reset_index()をした結果、元のインデックスが"index"列として含まれてしまうので落としておく

cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    xgb_reg = xgboost.XGBRegressor(
        #目的関数の指定 初期値も二乗誤差です
                        objective='reg:linear',
                        #学習のラウンド数 early_stoppingを利用するので多めに指定
                        n_estimators=50000,
                        #boosterに何を用いるか 初期値もgbtreeです
                        booster='gbtree',
                        #学習率
                        learning_rate=0.05,
                        #木の最大深さ
                        max_depth=7,
                        #シード値
                        random_state=0,
                            #正則化
                        reg_alfa=6.8594164113286965e-06,

                        sub_sample=0.16056047423047484,

                        colsample_bytree=0.6987351856651322,

                        min_child_weight=1.1103525577197584
    )
    xgb_reg.fit(X_tr, y_tr, eval_set=[(X_val, y_val)], early_stopping_rounds=10)
y_pred = xgb_reg.predict(X_test)

[14:23:52] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/objective/regression_obj.cu:203: reg:linear is now deprecated in favor of reg:squarederror.
[14:23:52] WARNING: /Users/runner/work/xgboost/xgboost/python-package/build/temp.macosx-11.0-arm64-cpython-38/xgboost/src/learner.cc:627: 
Parameters: { "reg_alfa", "sub_sample" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-rmse:131495.65061
[1]	validation_0-rmse:125467.57969
[2]	validation_0-rmse:119833.58280
[3]	validation_0-rmse:114430.11656
[4]	validation_0-rmse:109324.35206
[5]	validation_0-rmse:104585.29370
[6]	validation_0-rmse:99951.74782
[7]	validation_0-rmse:95452.08375
[8]	validation_0-rmse:91176.47006
[9]	va

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[14]	validation_0-rmse:70429.81813
[15]	validation_0-rmse:67614.34060
[16]	validation_0-rmse:64857.35232
[17]	validation_0-rmse:62225.78021
[18]	validation_0-rmse:59932.67819
[19]	validation_0-rmse:57578.11983
[20]	validation_0-rmse:55330.39440
[21]	validation_0-rmse:53234.41794
[22]	validation_0-rmse:51250.63979
[23]	validation_0-rmse:49462.65966
[24]	validation_0-rmse:47746.32929
[25]	validation_0-rmse:46126.12063
[26]	validation_0-rmse:44555.02305
[27]	validation_0-rmse:43171.03186
[28]	validation_0-rmse:41785.40705
[29]	validation_0-rmse:40474.81383
[30]	validation_0-rmse:39283.21024
[31]	validation_0-rmse:38088.87724
[32]	validation_0-rmse:37021.53150
[33]	validation_0-rmse:35988.56509
[34]	validation_0-rmse:35052.61495
[35]	validation_0-rmse:34221.09817
[36]	validation_0-rmse:33346.05596
[37]	validation_0-rmse:32610.35609
[38]	validation_0-rmse:31869.29951
[39]	validation_0-rmse:31117.91415
[40]	validation_0-rmse:30497.78447
[41]	validation_0-rmse:29851.84559
[42]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[15]	validation_0-rmse:67960.87261
[16]	validation_0-rmse:65198.28905
[17]	validation_0-rmse:62490.32992
[18]	validation_0-rmse:60284.84361
[19]	validation_0-rmse:57897.54143
[20]	validation_0-rmse:55612.03981
[21]	validation_0-rmse:53557.80547
[22]	validation_0-rmse:51525.86332
[23]	validation_0-rmse:49792.00980
[24]	validation_0-rmse:48122.96939
[25]	validation_0-rmse:46497.23662
[26]	validation_0-rmse:44808.89058
[27]	validation_0-rmse:43414.32124
[28]	validation_0-rmse:41972.26283
[29]	validation_0-rmse:40694.28679
[30]	validation_0-rmse:39574.54789
[31]	validation_0-rmse:38366.15691
[32]	validation_0-rmse:37354.45333
[33]	validation_0-rmse:36320.33013
[34]	validation_0-rmse:35467.48088
[35]	validation_0-rmse:34593.29464
[36]	validation_0-rmse:33764.71901
[37]	validation_0-rmse:33072.38139
[38]	validation_0-rmse:32421.02715
[39]	validation_0-rmse:31763.12908
[40]	validation_0-rmse:31185.43943
[41]	validation_0-rmse:30604.30808
[42]	validation_0-rmse:30023.66944
[43]	validation_0-rm

...

[14]	validation_0-rmse:70141.37310
[15]	validation_0-rmse:67134.53947
[16]	validation_0-rmse:64182.70840
[17]	validation_0-rmse:61453.72492
[18]	validation_0-rmse:59121.94725
[19]	validation_0-rmse:56686.73719
[20]	validation_0-rmse:54356.06543
[21]	validation_0-rmse:52175.04868
[22]	validation_0-rmse:50129.67109
[23]	validation_0-rmse:48235.17687
[24]	validation_0-rmse:46429.75835
[25]	validation_0-rmse:44711.07719
[26]	validation_0-rmse:43088.68216
[27]	validation_0-rmse:41624.12839
[28]	validation_0-rmse:40130.75216
[29]	validation_0-rmse:38796.80959
[30]	validation_0-rmse:37566.14527
[31]	validation_0-rmse:36338.74319
[32]	validation_0-rmse:35259.37957
[33]	validation_0-rmse:34193.56088
[34]	validation_0-rmse:33284.95917
[35]	validation_0-rmse:32409.95751
[36]	validation_0-rmse:31526.97194
[37]	validation_0-rmse:30799.29834
[38]	validation_0-rmse:30150.62243
[39]	validation_0-rmse:29407.41347
[40]	validation_0-rmse:28813.94355
[41]	validation_0-rmse:28229.78023
[42]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[11]	validation_0-rmse:79362.69384
[12]	validation_0-rmse:75903.27730
[13]	validation_0-rmse:72597.47382
[14]	validation_0-rmse:69568.15826
[15]	validation_0-rmse:66684.29604
[16]	validation_0-rmse:63880.98559
[17]	validation_0-rmse:61230.28784
[18]	validation_0-rmse:58961.78864
[19]	validation_0-rmse:56623.09939
[20]	validation_0-rmse:54363.91246
[21]	validation_0-rmse:52282.83742
[22]	validation_0-rmse:50284.78731
[23]	validation_0-rmse:48502.75779
[24]	validation_0-rmse:46815.46636
[25]	validation_0-rmse:45220.11077
[26]	validation_0-rmse:43692.10282
[27]	validation_0-rmse:42292.65552
[28]	validation_0-rmse:40890.27436
[29]	validation_0-rmse:39644.88716
[30]	validation_0-rmse:38508.32382
[31]	validation_0-rmse:37397.79491
[32]	validation_0-rmse:36331.88540
[33]	validation_0-rmse:35367.90813
[34]	validation_0-rmse:34518.52344
[35]	validation_0-rmse:33756.92874
[36]	validation_0-rmse:32959.75673
[37]	validation_0-rmse:32256.58591
[38]	validation_0-rmse:31638.49519
[39]	validation_0-rm

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/xgboost/sklearn.py:793: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[14]	validation_0-rmse:71725.57971
[15]	validation_0-rmse:68786.49251
[16]	validation_0-rmse:65825.17820
[17]	validation_0-rmse:63025.95261
[18]	validation_0-rmse:60695.91469
[19]	validation_0-rmse:58250.16589
[20]	validation_0-rmse:55837.78100
[21]	validation_0-rmse:53624.00816
[22]	validation_0-rmse:51461.46840
[23]	validation_0-rmse:49595.07327
[24]	validation_0-rmse:47786.55875
[25]	validation_0-rmse:46110.23842
[26]	validation_0-rmse:44401.79879
[27]	validation_0-rmse:42884.92645
[28]	validation_0-rmse:41327.21258
[29]	validation_0-rmse:39933.16038
[30]	validation_0-rmse:38649.88241
[31]	validation_0-rmse:37299.42414
[32]	validation_0-rmse:36210.83076
[33]	validation_0-rmse:35157.68128
[34]	validation_0-rmse:34209.66159
[35]	validation_0-rmse:33264.56143
[36]	validation_0-rmse:32310.27164
[37]	validation_0-rmse:31493.21378
[38]	validation_0-rmse:30790.36670
[39]	validation_0-rmse:29938.04745
[40]	validation_0-rmse:29334.26049
[41]	validation_0-rmse:28560.70936
[42]	validation_0-rm

In [3]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/XGB_cv_result.csv',index=False)